***PREPROCESSING***

In [650]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report, accuracy_score
from sklearn.linear_model import LogisticRegression
import folium



In [651]:
df=pd.read_csv(r"D:\project\townofcary-cpd-crash-incidents (1)\townofcary-cpd-crash-incidents\data\crash_data_1.csv")


In [652]:
df.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 23482 entries, 0 to 23481
Data columns (total 49 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   tamainid              23482 non-null  int64  
 1   location_description  23479 non-null  object 
 2   rdfeature             22888 non-null  object 
 3   rdcharacter           22896 non-null  object 
 4   rdclass               22899 non-null  object 
 5   rdconfigur            22817 non-null  object 
 6   rdsurface             22908 non-null  object 
 7   rdcondition           22896 non-null  object 
 8   lightcond             22928 non-null  object 
 9   weather               22925 non-null  object 
 10  trafcontrl            22866 non-null  object 
 11  lat                   5301 non-null   float64
 12  lon                   5301 non-null   float64
 13  lon2                  22811 non-null  float64
 14  lat2                  22783 non-null  float64
 15  tract              

In [653]:

df['contributing_factor'] = df['contributing_factor'].astype(str)

label_encoder = LabelEncoder()

df['contributing_factor_encoded'] = label_encoder.fit_transform(df['contributing_factor'])

print(df[['contributing_factor', 'contributing_factor_encoded']].head())

  contributing_factor  contributing_factor_encoded
0           NONE,NONE                           43
1           NONE,NONE                           43
2           NONE,NONE                           43
3           NONE,NONE                           43
4                NONE                           22


In [654]:
columns_to_drop = [
    'numpedestrians', 'contrcir2_desc', 'contrcir4_desc', 'vehicle3', 'vehicle4', 'vehicle5',
    'lon', 'lat', 'geo_location', 'tract', 'zone', 'vehicleconcat1', 'vehicleconcat2', 'vehicleconcat3', 'yearmonth', 'location','contrfact2', 'contrfact1',
     'crash_date', 'geo_location', 'contrcir3_desc', 'contrcir1_desc'
]

df = df.drop(columns=columns_to_drop)


In [655]:
pass_mean=np.ceil(df['numpassengers'].mean())
df['numpassengers'].fillna(pass_mean, inplace=True)

C:\Users\nevet\AppData\Local\Temp\ipykernel_26848\2720525040.py:2: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.





In [656]:
df['records'].drop_duplicates()
df['tamainid'].drop_duplicates()


0        48493
1        48494
2        48495
3        48500
4        48507
         ...  
23477    48438
23478    48442
23479    48464
23480    48485
23481    48486
Name: tamainid, Length: 23481, dtype: int64

In [657]:
df['numpassengers'] = df['numpassengers'].astype(int)

In [658]:
df = df[(df['lat2'] <= 90) & (df['lat2'] >= -90) & (df['lon2'] <= 720) & (df['lon2'] >= -360)]


In [659]:
df=df.dropna()

In [660]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 18796 entries, 0 to 23480
Data columns (total 29 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   tamainid                     18796 non-null  int64  
 1   location_description         18796 non-null  object 
 2   rdfeature                    18796 non-null  object 
 3   rdcharacter                  18796 non-null  object 
 4   rdclass                      18796 non-null  object 
 5   rdconfigur                   18796 non-null  object 
 6   rdsurface                    18796 non-null  object 
 7   rdcondition                  18796 non-null  object 
 8   lightcond                    18796 non-null  object 
 9   weather                      18796 non-null  object 
 10  trafcontrl                   18796 non-null  object 
 11  lon2                         18796 non-null  float64
 12  lat2                         18796 non-null  float64
 13  fatality             

***PLOTS***

The plot will show how the number of possible injuries and fatalities varies across different months. By observing the heights of the bars, one can identify which months have higher or lower incidents.


In [661]:
monthly_data = df.groupby('month').agg({'possblinj': 'sum', 'fatality': 'sum'}).reset_index()

# Melt the dataframe to plot using Plotly
monthly_data_melted = monthly_data.melt(id_vars='month', value_vars=['possblinj', 'fatality'], var_name='Type', value_name='Count')

fig = px.bar(monthly_data_melted, x='month', y='Count', color='Type', 
             title='Possible Injuries and Fatalities report on every month',
             labels={'month': 'Month', 'Count': 'Count', 'Type': 'Type'},
             category_orders={"month": ['Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']})
fig.update_layout(
    xaxis=dict(
        tickmode='array',
        tickvals=[1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12],
        ticktext=['Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']
    )
)

fig.show()

The following histograms uses Plotly to display the distribution of injuries across different categorical features related to road and environmental conditions. Each histogram compares the number of injuries under different conditions for each feature.

In [662]:
features = ['rdconfigur', 'rdsurface', 'rdcondition', 'lightcond', 'weather']

# Create a subplot for each feature
fig = px.histogram(df, x='rdconfigur', color='injuries', barmode='group', title='Injuries by Road Configuration')
fig.update_layout(xaxis_tickangle=-45)
fig.show()

fig = px.histogram(df, x='rdsurface', color='injuries', barmode='group', title='Injuries by Road Surface')
fig.show()

fig = px.histogram(df, x='rdcondition', color='injuries', barmode='group', title='Injuries by Road Condition')
fig.show()

fig = px.histogram(df, x='lightcond', color='injuries', barmode='group', title='Injuries by Light Condition')
fig.show()

fig = px.histogram(df, x='weather', color='injuries', barmode='group', title='Injuries by Weather Condition')
fig.show()

The following histograms uses Plotly to display the distribution of fatalities across different categorical features related to road and environmental conditions. Each histogram compares the number of fatalities under different conditions for each feature.

These plots help identify trends and patterns in how different road and environmental conditions affect fatality rates.

In [663]:
fig = px.histogram(df, x='rdconfigur', color='fatalities', barmode='group', title='Injuries by Road Configuration')
fig.update_layout(xaxis_tickangle=45)
fig.show()

fig = px.histogram(df, x='rdsurface', color='fatalities', barmode='group', title='Injuries by Road Surface')
fig.update_layout(xaxis_tickangle=45)
fig.show()

fig = px.histogram(df, x='rdcondition', color='fatalities', barmode='group', title='Injuries by Road Condition')
fig.show()

fig = px.histogram(df, x='lightcond', color='fatalities', barmode='group', title='Injuries by Light Condition')
fig.show()

fig = px.histogram(df, x='weather', color='fatalities', barmode='group', title='Injuries by Weather Condition')
fig.show()

A line graph that displays the monthly trend of the top 5 contributing factors to traffic incidents.
Overall trends over time can be observed for each contributing factor.
Certain contributing factors may exhibit peaks during specific months, indicating times when these factors are more prevalent. 

In [664]:
df['ta_date'] = pd.to_datetime(df['ta_date'])

# Extract month and year for aggregation
df['year_month'] = df['ta_date'].dt.to_period('M')

# Ensure fatalities is in boolean format
df['fatalities'] = df['fatalities'].astype(bool)

top_5_factors = df['contributing_factor_encoded'].value_counts().nlargest(5).index

df_top_5 = df[df['contributing_factor_encoded'].isin(top_5_factors)]

monthly_contributing_factors_top_5 = df_top_5.groupby(['year_month', 'contributing_factor_encoded']).size().reset_index(name='count')

# Convert year_month back to datetime for plotting
monthly_contributing_factors_top_5['year_month'] = monthly_contributing_factors_top_5['year_month'].dt.to_timestamp()

# Plot the line graph
fig = px.line(monthly_contributing_factors_top_5, x='year_month', y='count', color='contributing_factor_encoded',
              title='Monthly Trend of Top 5 Contributing Factors', labels={'contributing_factor_encoded': 'Contributing Factor'})

fig.update_layout(xaxis_title='Month', yaxis_title='Count of Contributing Factors')

# Show the plot
fig.show()

A scatter map using Plotly's scatter_mapbox to visualize the geographic distribution of injuries related to traffic incidents.
The scatter map shows clusters of injury incidents in specific geographic areas. These clusters indicate regions with a higher concentration of traffic incidents resulting in injuries.Areas with a dense cluster of points are high-risk zones where more traffic safety measures and enforcement might be needed.


In [665]:
filtered_df = df[(df['lat2'] <= 90) & (df['lat2'] >= -90) & (df['lon2'] <= 180) & (df['lon2'] >= -180)]

fig = px.scatter_mapbox(filtered_df, lat='lat2', lon='lon2', hover_name='injuries',color="injuries", zoom=10)
fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

fig.show()

The map shows specific locations where fatalities have occurred, marked by red icons. This can help identify fatality hotspots where multiple incidents have resulted in deaths.Identifying fatality hotspots allows for targeted safety interventions, such as redesigning problematic intersections, enhancing road lighting, and adding safety barriers.


In [666]:
map_fatality = folium.Map(location=[df['lat2'].mean(), df['lon2'].mean()], zoom_start=10)

for index, row in df.iterrows():
    if row['fatalities']:
        folium.Marker([row['lat2'], row['lon2']], popup=row['location_description'], icon=folium.Icon(color='red')).add_to(map_fatality)

map_fatality


In [667]:
df['rdsurface'].unique()

array(['SMOOTH ASPHALT', 'COARSE ASPHALT', 'GROOVED CONCRETE', 'CONCRETE',
       'SOIL', 'GRAVEL', 'OTHER *'], dtype=object)

***Model***

The following model processes and prepares the data, then trains a RandomForestClassifier to predict road surface types (rdsurface) based on various features

In [668]:
# Convert 'ta_date' to datetime and extract useful features
filtered_df['ta_date'] = pd.to_datetime(filtered_df['ta_date'], errors='coerce')
filtered_df['ta_year'] = filtered_df['ta_date'].dt.year
filtered_df['ta_month'] = filtered_df['ta_date'].dt.month
filtered_df['ta_day'] = filtered_df['ta_date'].dt.day

# Drop the original datetime column and any other non-relevant or identifier columns
filtered_df = filtered_df.drop(columns=['tamainid', 'ta_date', 'ta_time'])

# Encode categorical features
label_encoders = {}
categorical_features = ['location_description', 'rdfeature', 'rdcharacter', 'rdclass', 'rdconfigur', 'rdcondition', 
                        'lightcond', 'weather', 'trafcontrl', 'vehicle1', 'vehicle2', 'workarea', 'contributing_factor', 
                        'vehicle_type']

for feature in categorical_features:
    le = LabelEncoder()
    filtered_df[feature] = le.fit_transform(filtered_df[feature].astype(str))
    label_encoders[feature] = le

# Encode the target variable 'rdsurface'
le_rdsurface = LabelEncoder()
filtered_df['rdsurface'] = le_rdsurface.fit_transform(filtered_df['rdsurface'])

# Remove classes with fewer than 2 samples
min_class_samples = 2
filtered_df = filtered_df[filtered_df['rdsurface'].isin(class_counts[class_counts >= min_class_samples].index)]

# Define features and target
X = filtered_df.drop(columns=['rdsurface'])
y = filtered_df['rdsurface']

# Ensure all remaining columns are numeric
X = X.apply(pd.to_numeric, errors='coerce')

X = X.fillna(0)

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)

# Scale features
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Initialize and train the RandomForestClassifier
clf = RandomForestClassifier(n_estimators=100, random_state=42)
clf.fit(X_train, y_train)

y_pred = clf.predict(X_test)

# Get the updated class labels
updated_class_labels = le_rdsurface.inverse_transform(sorted(y.unique()))

print("Accuracy:", accuracy_score(y_test, y_pred))
print("Classification Report:\n", classification_report(y_test, y_pred, target_names=updated_class_labels))





Accuracy: 0.8347964884277733
Classification Report:
                   precision    recall  f1-score   support

  COARSE ASPHALT       0.74      0.08      0.14       479
        CONCRETE       0.37      0.12      0.18       106
          GRAVEL       0.00      0.00      0.00         5
GROOVED CONCRETE       0.35      0.17      0.23        54
         OTHER *       1.00      0.50      0.67         2
  SMOOTH ASPHALT       0.84      0.99      0.91      3113

        accuracy                           0.83      3759
       macro avg       0.55      0.31      0.35      3759
    weighted avg       0.81      0.83      0.78      3759



C:\Users\nevet\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\sklearn\metrics\_classification.py:1509: UndefinedMetricWarning:

Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.

C:\Users\nevet\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\sklearn\metrics\_classification.py:1509: UndefinedMetricWarning:

Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.

C:\Users\nevet\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\sklearn\metrics\_classification.py:1509: UndefinedMetricWarning:

Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` pa

The following model processes and prepares the data, then trains a LogisticRegression model to predict injuries (injuries) based on various features. 

In [669]:
# Convert 'ta_date' to datetime and extract useful features
df['ta_date'] = pd.to_datetime(df['ta_date'], errors='coerce')
df['ta_year'] = df['ta_date'].dt.year
df['ta_month'] = df['ta_date'].dt.month
df['ta_day'] = df['ta_date'].dt.day

# Drop the original datetime columns
df = df.drop(columns=['tamainid', 'ta_date', 'ta_time'])

# Encode categorical features
label_encoders = {}
categorical_features = ['location_description', 'rdfeature', 'rdcharacter', 'rdclass', 'rdconfigur', 'rdcondition', 
                        'lightcond', 'weather', 'trafcontrl', 'vehicle1', 'vehicle2', 'workarea', 'contributing_factor', 
                        'vehicle_type']

for feature in categorical_features:
    le = LabelEncoder()
    df[feature] = le.fit_transform(df[feature].astype(str))
    label_encoders[feature] = le

# Define features and target
X = df.drop(columns=['injuries'])
y = df['injuries']

# Ensure all remaining columns are numeric
X = X.apply(pd.to_numeric, errors='coerce')

# Handle any remaining NaNs
X = X.fillna(0)

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)

# Scale features
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Initialize and train the LogisticRegression
clf = LogisticRegression(max_iter=1000, random_state=42)
clf.fit(X_train, y_train)

y_pred = clf.predict(X_test)

print("Accuracy:", accuracy_score(y_test, y_pred))
print("Classification Report:\n", classification_report(y_test, y_pred))


Accuracy: 1.0
Classification Report:
               precision    recall  f1-score   support

       False       1.00      1.00      1.00      3249
        True       1.00      1.00      1.00       511

    accuracy                           1.00      3760
   macro avg       1.00      1.00      1.00      3760
weighted avg       1.00      1.00      1.00      3760

